In [ ]:
%%capture
!git clone https://github.com/hammaad2002/ASRAdversarialAttacks.git
!git clone https://github.com/hammaad2002/CRDNN_Model.git
%cd /content/ASRAdversarialAttacks/
!pip install -r requirements.txt

In [ ]:
from ASRAdversarialAttacks.AdversarialAttacks import ASRAttacks
import torchaudio
import torch
import numpy as np
from IPython.display import Audio

In [ ]:
# Loading the model from torchaudio model hub
bundle = torchaudio.pipelines.WAV2VEC2_ASR_BASE_960H
model = bundle.get_model()

Downloading: "https://download.pytorch.org/torchaudio/models/wav2vec2_fairseq_base_ls960_asr_ls960.pth" to /root/.cache/torch/hub/checkpoints/wav2vec2_fairseq_base_ls960_asr_ls960.pth
100%|██████████| 360M/360M [00:04<00:00, 80.4MB/s]


In [ ]:
# Checking the device available during the current environment (CUDA is recommended!)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = model.to(device)

In [ ]:
# Loading the audio
input_audio, sample_rate = torchaudio.load('/content/CRDNN_Model/AudioSamplesASR/spk1_snt1.wav')

In [ ]:
# My target
target_transcription = 'WHEN MAN NOTHING KILL IN BIG CAMEL'
true_transcription = 'THE CHILD ALMOST HURT THE SMALL DOG'
attack = ASRAttacks(model, device, bundle.get_labels())
target = list(target_transcription.upper().replace(" ", "|"))

In [ ]:
#initializing attack class
attack = ASRAttacks(model, device, bundle.get_labels())

# <center>**FGSM ATTACK**</center>

```
        Simple fast gradient sign method attack is implemented which is the simplest
        adversarial attack in this domain.
        For more information, see the paper: https://arxiv.org/pdf/1412.6572.pdf

        INPUT ARGUMENTS:

        input__       : Input audio. Ex: Tensor[0.1,0.3,...] or (samples,)
                        Type: torch.Tensor

        target        : Target transcription (needed if the you want targeted
                        attack) Ex: ["my name is mango."].
                        Type: List[str]
                        CAUTION:
                        Please make sure these characters are also present in the
                        dictionary of the model also.

        epsilon       : Noise controlling parameter.
                        Type: float

        targeted      : If the attack should be targeted towards your desired
                        transcription or not.
                        Type: bool
                        CAUTION:
                        Please make to pass your targetted
                        transcription also in this case).

        RETURNS:

        np.ndarray : Perturbed audio
```


# **FGSM TARGETED**

In [ ]:
#FGSM
temp1 = attack.FGSM_ATTACK(input_audio, target, epsilon = 0.01, targeted = True)

#FGSM PRINT
print(attack.INFER(torch.from_numpy(temp1)).replace("|"," "))
print(target_transcription)

THE CHILD ALMOST HURT A SMALL GOG 
WHEN MAN NOTHING KILL IN BIG CAMEL


For WER use [0] and for in depth information of insertion, selection, and deletion use [1]

In [ ]:
print("Targeted WER is: ", attack.wer_compute([target_transcription], [temp1], targeted= True)[0])

Targeted WER is:  0.0


In [ ]:
info = attack.wer_compute([target_transcription], [temp1], targeted= True)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 0, Substitution: 7, Deletion: 0


In [ ]:
# FGSM TARGETED
Audio(temp1, rate =16000)

# **FGSM UNTARGETED**

In [ ]:
#FGSM
temp2 = attack.FGSM_ATTACK(input_audio, epsilon = 0.0065, targeted = False)

#FGSM PRINT
print(attack.INFER(torch.from_numpy(temp2)).replace("|"," "))

THE CHILD ALMOST HURT  THE SMALL DOG 


In [ ]:
print("Untargeted WER is: ", attack.wer_compute([target_transcription], [temp2], targeted= False)[0])

Untargeted WER is:  1.0


In [ ]:
info = attack.wer_compute([target_transcription], [temp2], targeted= False)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 0, Substitution: 7, Deletion: 0


In [ ]:
#FGSM UNTARGETED
Audio(temp2, rate =16000)

# <center>**BIM ATTACK**</center>

```
        Basic Itertive Moment attack is implemented which is simple Fast Gradient
        Sign Attack but in loop.
        For more information, see the paper: https://arxiv.org/abs/1607.02533

        INPUT ARGUMENTS:

        input__       : Input audio. Ex: Tensor[0.1,0.3,...] or (samples,)
                        Type: torch.Tensor

        target        : Target transcription (needed if the you want targeted
                        attack) Ex: ["my name is mango."].
                        Type: List[str]
                        CAUTION:
                        Please make sure these characters are also present in the
                        dictionary of the model also.

        epsilon       : Noise controlling parameter.
                        Type: float

        alpha         : Noise contribution in input controlling parameter
                        Type: float

        num_iter      : Number of iteration of attack
                        Type: int

        targeted      : If the attack should be targeted towards your desired
                        transcription or not.
                        Type: bool
                        CAUTION:
                        Please make to pass your targetted
                        transcription also in this case).

        early_stop    : If user wants to stop the attack early if the attack reaches the target transcription before the total number of iterations.
                        Type: bool
                        
        RETURNS:
        
        np.ndarray : Perturbed audio
```


# **BIM TARGETED**

With early stopping:

In [ ]:
#BIM
temp3 = attack.BIM_ATTACK(input_audio, target, epsilon = 0.0015, alpha = 0.00009,
                   num_iter = 3000, targeted = True, early_stop = True)

#BIM PRINT
print('\n',attack.INFER(torch.from_numpy(temp3)).replace("|"," "))
print(target_transcription)

  0%|          | 0/3000 [00:00<?, ?it/s]

Breaking for loop because targeted Attack is performed successfully !

 WHEN MAN NOTHING KILL IN BIG CAMEL
WHEN MAN NOTHING KILL IN BIG CAMEL


In [ ]:
print("Targeted WER is: ", attack.wer_compute([target_transcription], [temp3], targeted= True)[0])

Targeted WER is:  1.0


In [ ]:
info = attack.wer_compute([target_transcription], [temp3], targeted= True)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 0, Substitution: 0, Deletion: 0


In [ ]:
#BIM TARGETED with early stopping
Audio(temp3, rate = 16000)

Without early stopping:

In [ ]:
#BIM
temp4 = attack.BIM_ATTACK(input_audio, target, epsilon = 0.0015, alpha = 0.00009,
                   num_iter = 3000, targeted = True, early_stop = False)

#BIM PRINT
print('\n',attack.INFER(torch.from_numpy(temp4)).replace("|"," "))
print(target_transcription)

  0%|          | 0/3000 [00:00<?, ?it/s]


 WHEN MAN NOTHING KILL IN BIG CAMEL
WHEN MAN NOTHING KILL IN BIG CAMEL


In [ ]:
print("Targeted WER is: ", attack.wer_compute([target_transcription], [temp4], targeted= True)[0])

Targeted WER is:  1.0


In [ ]:
info = attack.wer_compute([target_transcription], [temp4], targeted= True)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 0, Substitution: 0, Deletion: 0


In [ ]:
#BIM TARGETED without early stopping
Audio(temp4, rate = 16000)

# **BIM UNTARGETED**

With early stopping:

In [ ]:
#BIM
temp5 = attack.BIM_ATTACK(input_audio, epsilon = 0.0015, alpha = 0.00009,
                   num_iter = 2500, targeted = False, early_stop = True)

#BIM PRINT
print('\n',attack.INFER(torch.from_numpy(temp5)).replace("|"," "))

  0%|          | 0/2500 [00:00<?, ?it/s]

Breaking for loop because untargeted Attack is performed successfully !

 CHILD ALMOST HURT THE SMALL DOG 


In [ ]:
print("Untargeted WER is: ", attack.wer_compute([target_transcription], [temp5], targeted= False)[0])

Untargeted WER is:  1.0


In [ ]:
info = attack.wer_compute([target_transcription], [temp5], targeted= False)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 0, Substitution: 6, Deletion: 1


In [ ]:
#BIM UNTARGETED with early stopping
Audio(temp5, rate =16000)

Without early stopping:

In [ ]:
#BIM
temp6 = attack.BIM_ATTACK(input_audio, epsilon = 0.0015, alpha = 0.00009,
                   num_iter = 2500, targeted = False, early_stop = False)

#BIM PRINT
print('\n',attack.INFER(torch.from_numpy(temp6)).replace("|"," "))

  0%|          | 0/2500 [00:00<?, ?it/s]


 IT EAT HAEUTIEDITA A UAMN ATIEI UIE E IKUIEKW TAEITMARA U WADE ADA B UTRTI


In [ ]:
print("Untargeted WER is: ", attack.wer_compute([target_transcription], [temp6], targeted= False)[0])

Untargeted WER is:  1.0


In [ ]:
info = attack.wer_compute([target_transcription], [temp6], targeted= False)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 8, Substitution: 7, Deletion: 0


In [ ]:
#BIM UNTARGETED without early stopping
Audio(temp6, rate =16000)

# <center>**PGD ATTACK**</center>

```
        Projected Gradient Descent attack is implemented which in simple terms is more
        advanced version of BIM. In this attack we project our perturbation back to
        some Lp norm and find perturbations in that particular region.
        For more information, see the paper: https://arxiv.org/abs/1706.06083

        INPUT ARGUMENTS:

        input__       : Input audio. Ex: Tensor[0.1,0.3,...] or (samples,)
                        Type: torch.Tensor

        target        : Target transcription (needed if the you want targeted
                        attack) Ex: ["my name is mango."].
                        Type: List[str]
                        CAUTION:
                        Please make sure these characters are also present in the
                        dictionary of the model also.

        epsilon       : Noise controlling parameter.
                        Type: float

        alpha         : Noise contribution in input controlling parameter
                        Type: float

        num_iter      : Number of iteration of attack
                        Type: int

        targeted      : If the attack should be targeted towards your desired
                        transcription or not.
                        Type: bool
                        CAUTION:
                        Please make to pass your targetted
                        transcription also in this case).

        early_stop    : If user wants to stop the attack early if the attack reaches the target transcription before the total number of iterations.
                        Type: bool
                        
        RETURNS:
        
        np.ndarray : Perturbed audio
```

# **PGD TARGETED**

With early stopping:

In [ ]:
#PGD
temp7 = attack.PGD_ATTACK(input_audio, target, epsilon = 0.0015, alpha = 0.00009,
                   num_iter = 2500, targeted = True, early_stop = True)

#PGD PRINT
print('\n',attack.INFER(torch.from_numpy(temp7)).replace("|"," "))
print(target_transcription)

  0%|          | 0/2500 [00:00<?, ?it/s]


 CHIL MA NOTHING KWILL IN BAG CAME
WHEN MAN NOTHING KILL IN BIG CAMEL


In [ ]:
print("Targeted WER is: ", attack.wer_compute([target_transcription], [temp7], targeted= True)[0])

Targeted WER is:  0.2857142857142857


In [ ]:
info = attack.wer_compute([target_transcription], [temp7], targeted= True)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 0, Substitution: 5, Deletion: 0


In [ ]:
#PGD TARGETED with early stopping
Audio(temp7, rate =16000)

Without early stopping:

In [ ]:
#PGD
temp8 = attack.PGD_ATTACK(input_audio, target, epsilon = 0.0015, alpha = 0.00009,
                   num_iter = 2500, targeted = True, early_stop = False)

#PGD PRINT
print('\n',attack.INFER(torch.from_numpy(temp8)).replace("|"," "))
print(target_transcription)

  0%|          | 0/2500 [00:00<?, ?it/s]


 WHAEN MAN NOTHING KNALL IN BI CAME
WHEN MAN NOTHING KILL IN BIG CAMEL


In [ ]:
print("Targeted WER is: ", attack.wer_compute([target_transcription], [temp8], targeted= True)[0])

Targeted WER is:  0.4285714285714286


In [ ]:
info = attack.wer_compute([target_transcription], [temp8], targeted= True)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 0, Substitution: 4, Deletion: 0


In [ ]:
#PGD TARGETED without early stopping
Audio(temp8, rate =16000)

# **PGD UNTARGETED**

With early stopping:

In [ ]:
#PGD
temp9 = attack.PGD_ATTACK(input_audio, epsilon = 0.0015, alpha = 0.0001,
                   num_iter = 10000, targeted = False, early_stop = True)

#PGD PRINT
print('\n',attack.INFER(torch.from_numpy(temp9)).replace("|"," "))

  0%|          | 0/10000 [00:00<?, ?it/s]


 THE CHILD'S ALMOST HAEART GAVE THE SMALL JAWAWS 


In [ ]:
print("Untargeted WER is: ", attack.wer_compute([target_transcription], [temp9], targeted= False)[0])

Untargeted WER is:  1.0


In [ ]:
info = attack.wer_compute([target_transcription], [temp9], targeted= False)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 1, Substitution: 7, Deletion: 0


In [ ]:
#PGD UNTARGETED with early stopping
Audio(temp9, rate =16000)

Without early stopping:

In [ ]:
#PGD
temp10 = attack.PGD_ATTACK(input_audio, epsilon = 0.0015, alpha = 0.0001,
                   num_iter = 10000, targeted = False, early_stop = True)

#PGD PRINT
print('\n',attack.INFER(torch.from_numpy(temp10)).replace("|"," "))

  0%|          | 0/10000 [00:00<?, ?it/s]


 THE CHILD ALMOST TIRT WWIITH A SMIILE MNOD 


In [ ]:
print("Untargeted WER is: ", attack.wer_compute([target_transcription], [temp10], targeted= False)[0])

Untargeted WER is:  1.0


In [ ]:
info = attack.wer_compute([target_transcription], [temp10], targeted= False)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 1, Substitution: 7, Deletion: 0


In [ ]:
#PGD UNTARGETED without early stopping
Audio(temp10, rate =16000)

# <center>**CW ATTACK**</center>

```
        Implements the Carlini and Wagner attack, the strongest white box
        adversarial attack. This attack uses an optimization strategy to find the
        adversarial transcription while keeping the perturbation as low as possible.
        For more information, see the paper: https://arxiv.org/pdf/1801.01944.pdf
        
        INPUT ARGUMENTS:
        
        input__       : Input audio. Ex: Tensor[0.1,0.3,...] or (samples,)
                        Type: torch.Tensor
                        
        target        : Target transcription (needed if the you want targeted
                        attack) Ex: ["my name is mango."].
                        Type: List[str]
                        CAUTION:
                        Please make sure these characters are also present in the
                        dictionary of the model also.
                        
        epsilon       : Noise controlling parameter.
                        Type: float
                        
        c             : Regularization term controlling factor.
                        Type: float
                        
        learning_rate : learning_rate of optimizer.
                        Type: float
                        
        num_iter      : Number of iteration of attack.
                        Type: int
                        
        decrease_factor_eps   : Factor to decrease epsilon during search
                                Type: float
                                
        num_iter_decrease_eps : Number of iterations after which to decrease epsilon
                                Type: int
                                
        optimizer     : Name of the optimizer to use for the attack.
                        Type: str
                        
        nested        : if this attack in being run in a for loop with tqdm
                        Type: bool
                        
        early_stop    : if the user wants to end the attack as soon as the attack
                        gets the target transcription.
                        Type: bool
                        
        search_eps    : if the user wants the attack to search for the epsilon value
                        on its own provided the initial epsilon value of large.
                        Type: bool
        
        targeted      : If the attack should be targeted towards your desired
                        transcription or not.
                        Type: bool
                        CAUTION:
                        Please make to pass your targetted
                        transcription also in this case).
                        
        RETURNS:
        
        np.ndarray : Perturbed audio
```

# **CW TARGETED**

With early stopping:

In [ ]:
#CW
temp11 = attack.CW_ATTACK(input_audio, target, epsilon = 0.0015, c = 10,
                  learning_rate = 0.00001, num_iter = 10000, decrease_factor_eps = 1,
                  num_iter_decrease_eps = 10, optimizer = None, nested = True,
                  early_stop = True, search_eps = False, targeted = True)

#CW PRINT
print('\n',attack.INFER(torch.from_numpy(temp11)).replace("|"," "))
print(target_transcription)

  0%|          | 0/10000 [00:00<?, ?it/s]

Breaking for loop because targeted Attack is performed successfully !

 WHEN MAN NOTHING KILL IN BIG CAMEL
WHEN MAN NOTHING KILL IN BIG CAMEL


In [ ]:
print("Targeted WER is: ", attack.wer_compute([target_transcription], [temp11], targeted= True)[0])

Targeted WER is:  1.0


In [ ]:
info = attack.wer_compute([target_transcription], [temp11], targeted= True)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 0, Substitution: 0, Deletion: 0


In [ ]:
#CW TARGETED with early stopping
Audio(temp11, rate =16000)

Without early stopping:

In [ ]:
#CW
temp12 = attack.CW_ATTACK(input_audio, target, epsilon = 0.0015, c = 10,
                  learning_rate = 0.00001, num_iter = 10000, decrease_factor_eps = 1,
                  num_iter_decrease_eps = 10, optimizer = None, nested = True,
                  early_stop = False, search_eps = False, targeted = True)

#CW PRINT
print('\n',attack.INFER(torch.from_numpy(temp12)).replace("|"," "))
print(target_transcription)

  0%|          | 0/10000 [00:00<?, ?it/s]


 CHEN MAN NOTHING KILL IN BIG CAMEL
WHEN MAN NOTHING KILL IN BIG CAMEL


In [ ]:
print("Targeted WER is: ", attack.wer_compute([target_transcription], [temp12], targeted= True)[0])

Targeted WER is:  0.8571428571428572


In [ ]:
info = attack.wer_compute([target_transcription], [temp12], targeted= True)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 0, Substitution: 1, Deletion: 0


In [ ]:
#CW TARGETED without early stopping
Audio(temp12, rate =16000)

# **CW UNTARGETED**

With early stopping:

In [ ]:
#CW
temp13 = attack.CW_ATTACK(input_audio, epsilon = 0.0015, c = 10,
                  learning_rate = 0.00001, num_iter = 10000, decrease_factor_eps = 1,
                  num_iter_decrease_eps = 10, optimizer = None, nested = True,
                  early_stop = True, search_eps = False, targeted = False)

#CW PRINT
print('\n',attack.INFER(torch.from_numpy(temp13)).replace("|"," "))

  0%|          | 0/10000 [00:00<?, ?it/s]

Breaking for loop because targeted Attack is performed successfully !

 THECHILD' ALMOST HHURTRTHE SMALL DOG 


In [ ]:
print("Untargeted WER is: ", attack.wer_compute([target_transcription], [temp13], targeted= False)[0])

Untargeted WER is:  1.0


In [ ]:
info = attack.wer_compute([target_transcription], [temp13], targeted= False)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 0, Substitution: 5, Deletion: 2


In [ ]:
#CW UNTARGETED with early stopping
Audio(temp13, rate =16000)

Without early stopping:

In [ ]:
#CW
temp14 = attack.CW_ATTACK(input_audio, epsilon = 0.0015, c = 10,
                  learning_rate = 0.00001, num_iter = 10000, decrease_factor_eps = 1,
                  num_iter_decrease_eps = 10, optimizer = None, nested = True,
                  early_stop = False, search_eps = False, targeted = False)

#CW PRINT
print('\n',attack.INFER(torch.from_numpy(temp14)).replace("|"," "))

  0%|          | 0/10000 [00:00<?, ?it/s]


 EAN IN E A NA AON OT N RERURERNRA A IN A N DON O R AE


In [ ]:
print("Untargeted WER is: ", attack.wer_compute([target_transcription], [temp14], targeted= False)[0])

Untargeted WER is:  1.0


In [ ]:
info = attack.wer_compute([target_transcription], [temp14], targeted= False)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 10, Substitution: 7, Deletion: 0


In [ ]:
#CW UNTARGETED without early stopping
Audio(temp14, rate = 16000)

# <center>**IMPERCEPTIBLE ASR ATTACK**</center>


```
        Implements the Imperceptible ASR attack, which leverages the strongest white box
        adversarial attack which is CW attack while also masking sure the added perturbation
        is imperceptible to humans using Psychoacoustic Scale. This attack is performed in two
        stages. In first stage we perform simple CW attack and in 2nd stage we make sure our
        added perturbations are imperceptible.
        For more information, see the paper: https://arxiv.org/abs/1903.10346
        
        INPUT ARGUMENTS:
        
        input__       : Input audio. Ex: Tensor[0.1,0.3,...] or (samples,)
                        Type: torch.Tensor
                        
        target        : Target transcription (needed if the you want targeted
                        attack) Ex: ["my name is mango."]
                        Type: List[str]
                        CAUTION:
                        Please make sure these characters are also present in the
                        dictionary of the model also
                        
        epsilon       : Noise controlling parameter
                        Type: float
                        
        c             : Regularization term controlling factor
                        Type: float
                        
        learning_rate1: learning_rate of optimizer for stage 1
                        Type: float
        
        learning_rate2: learning_rate of optimizer for stage 2
                        Type: float
                        
        num_iter1     : Number of iteration of attack stage 1
                        Type: int
        
        num_iter2     : Number of iteration of attack stage 2
                        Type: int
                        
        decrease_factor_eps   : Factor to decrease epsilon by during optimization
                                Type: float
                                
        num_iter_decrease_eps : Number of iterations after which to decrease epsilon
                                Type: int
                                
        optimizer1     : Name of the optimizer to use for the attack stage 1
                         Type: str
                         
        optimizer2     : Name of the optimizer to use for the attack stage 2
                         Type: str
                         
        nested         : if this attack in being run in a for loop with tqdm
                         Type: bool
        
        early_stop_cw  : if the user wants 1st stage attack to early stop or not
                         Type: bool
        
        search_eps_cw  : if the user wants 1st stage attack to search for epsilon
                         value provided a large intial epsilon value is provided
                         Type: bool
                         
        alpha          : regularization term for second stage loss
                         Type: float
                         
        RETURNS:
        
        np.ndarray     : Perturbed audio
```

With early stopping:

In [ ]:
temp15 = attack.IMPERCEPTIBLE_ATTACK(torch.nn.functional.pad(input_audio, (0, 1000)), target, epsilon = 0.015, c = 10, learning_rate1 = 0.001,
                                    learning_rate2 = 0.0001, num_iter1 = 1000, num_iter2 = 15000, decrease_factor_eps = 1,
                                    num_iter_decrease_eps = 10, optimizer1 = None, optimizer2 = "Adam",nested = True ,
                                    early_stop_cw = True, search_eps_cw = False, alpha = 0.05)

# Attack's transcription
print('\n',attack.INFER(torch.from_numpy(temp15)).replace("|"," "))

*****Attack Stage 1*****:   0%|          | 0/1000 [00:00<?, ?it/s]

*****Attack Stage 2*****:   0%|          | 0/15000 [00:00<?, ?it/s]


 WHEN MAN NOTHING KILL IN BIG CAMEL


In [ ]:
print("Targeted WER is: ", attack.wer_compute([target_transcription], [temp15], targeted= True)[0])

Targeted WER is:  1.0


In [ ]:
info = attack.wer_compute([target_transcription], [temp15], targeted= True)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 0, Substitution: 0, Deletion: 0


In [ ]:
#IMPERCPTIBLE TARGETED with early stopping
Audio(temp15[:,:-1000], rate = 16000)

Without early stopping:

In [ ]:
temp16 = attack.IMPERCEPTIBLE_ATTACK(torch.nn.functional.pad(input_audio, (0, 1000)), target, epsilon = 0.015, c = 10, learning_rate1 = 0.001,
                                    learning_rate2 = 0.0001, num_iter1 = 1000, num_iter2 = 15000, decrease_factor_eps = 1,
                                    num_iter_decrease_eps = 10, optimizer1 = None, optimizer2 = "Adam",nested = True ,
                                    early_stop_cw = False, search_eps_cw = False, alpha = 0.05)

# Attack's transcription
print('\n',attack.INFER(torch.from_numpy(temp16)).replace("|"," "))

*****Attack Stage 1*****:   0%|          | 0/1000 [00:00<?, ?it/s]

*****Attack Stage 2*****:   0%|          | 0/15000 [00:00<?, ?it/s]


 WHEND MAN NOTHING KILL IN BIG CAMEL


In [ ]:
print("Targeted WER is: ", attack.wer_compute([target_transcription], [temp16], targeted= True)[0])

Targeted WER is:  0.8571428571428572


In [ ]:
info = attack.wer_compute([target_transcription], [temp16], targeted= True)[1]
print(f"Insertion: {info[0][1]}, Substitution: {info[0][0]}, Deletion: {info[0][2]}")

Insertion: 0, Substitution: 0, Deletion: 0


In [ ]:
#IMPERCPTIBLE TARGETED without early stopping
Audio(temp16[:,:-1000], rate = 16000)

----------------------------

# <center> **COMPARISON**

METRIC I USED FOR COMPARISON

In [ ]:
# SNR metric for comparison to check which attack adds less noise
def Metricsnr(original, noisy):
    original_power = 20 * np.log10(np.mean(original ** 2))
    noise_power = 20 * np.log10(np.mean((original - noisy) ** 2))
    snr = noise_power - original_power
    return snr

In [ ]:
orig = input_audio.numpy() # clean audio
orig.shape

(1, 45920)

-------------------

# **TARGETED ATTACKS**

In [ ]:
Audio(temp1, rate =16000) #FGSM targeted

In [ ]:
print("LOWER SNR IS BETTER OVER BECAUSE OF THE WAY IT IS MEASURED")
print("FGSM SNR                  :",Metricsnr(orig, temp1))

LOWER SNR IS BETTER OVER BECAUSE OF THE WAY IT IS MEASURED
FGSM SNR                  : -14.40436840057373


With early stopping

In [ ]:
Audio(temp3, rate = 16000) #BIM targeted

In [ ]:
Audio(temp7, rate = 16000) #PGD targeted

In [ ]:
Audio(temp11, rate = 16000) #CW targeted

In [ ]:
Audio(temp15[:,:-1000], rate = 16000) # Imperceptible ASR

In [ ]:
print("LOWER SNR IS BETTER OVER BECAUSE OF THE WAY IT IS MEASURED")
print("BIM SNR                  :",Metricsnr(orig, temp3))
print("PGD SNR                  :",Metricsnr(orig, temp7))
print("CW SNR                   :",Metricsnr(orig, temp11))
print("IMPERCEPTIBLE ATTACK SNR :",Metricsnr(orig, temp15[:,:-1000]))

LOWER SNR IS BETTER OVER BECAUSE OF THE WAY IT IS MEASURED
BIM SNR                  : -38.70874881744385
PGD SNR                  : -52.756638526916504
CW SNR                   : -57.65882968902588
IMPERCEPTIBLE ATTACK SNR : nan


Without early stopping

In [ ]:
Audio(temp4, rate = 16000) #BIM targeted

In [ ]:
Audio(temp8, rate = 16000) #PGD targeted

In [ ]:
Audio(temp12, rate = 16000) #CW targeted

In [ ]:
Audio(temp16[:,:-1000], rate = 16000) # Imperceptible ASR

In [ ]:
print("LOWER SNR IS BETTER OVER BECAUSE OF THE WAY IT IS MEASURED")
print("BIM SNR                  :",Metricsnr(orig, temp4))
print("PGD SNR                  :",Metricsnr(orig, temp8))
print("CW SNR                   :",Metricsnr(orig, temp12))
print("IMPERCEPTIBLE ATTACK SNR :",Metricsnr(orig, temp16[:,:-1000]))

LOWER SNR IS BETTER OVER BECAUSE OF THE WAY IT IS MEASURED
BIM SNR                  : -22.978615760803223
PGD SNR                  : -52.32065677642822
CW SNR                   : -56.628432273864746
IMPERCEPTIBLE ATTACK SNR : -33.190226554870605


-------------------

-------------------

# **UNTARGETED ATTACKS**

In [ ]:
Audio(temp2, rate =16000) #FGSM untargeted

In [ ]:
print("LOWER SNR IS BETTER OVER BECAUSE OF THE WAY IT IS MEASURED")
print("FGSM SNR:",Metricsnr(orig, temp2))

LOWER SNR IS BETTER OVER BECAUSE OF THE WAY IT IS MEASURED
FGSM SNR: -21.887822151184082


With early stopping

In [ ]:
Audio(temp5, rate = 16000) #BIM untargeted

In [ ]:
Audio(temp9, rate = 16000) #PGD untargeted

In [ ]:
Audio(temp13, rate = 16000) #CW untargeted

In [ ]:
print("LOWER SNR IS BETTER OVER BECAUSE OF THE WAY IT IS MEASURED")
print("BIM SNR:",Metricsnr(orig, temp5))
print("PGD SNR:",Metricsnr(orig, temp9))
print("CW SNR :",Metricsnr(orig, temp13))

LOWER SNR IS BETTER OVER BECAUSE OF THE WAY IT IS MEASURED
BIM SNR: -78.14002513885498
PGD SNR: -52.284531593322754
CW SNR : -94.0333890914917


Without early stopping

In [ ]:
Audio(temp6, rate = 16000) #BIM untargeted

In [ ]:
Audio(temp10, rate = 16000) #PGD untargeted

In [ ]:
Audio(temp14, rate = 16000) #PGD untargeted

In [ ]:
print("LOWER SNR IS BETTER OVER BECAUSE OF THE WAY IT IS MEASURED")
print("BIM SNR:",Metricsnr(orig, temp6))
print("PGD SNR:",Metricsnr(orig, temp10))
print("CW SNR :",Metricsnr(orig, temp14))

LOWER SNR IS BETTER OVER BECAUSE OF THE WAY IT IS MEASURED
BIM SNR: -24.528326988220215
PGD SNR: -52.332472801208496
CW SNR : -56.36096477508545


-------------------